In [2]:
# import netrc  # no need to install, just import

# info = netrc.netrc()
# username, _, password = info.authenticators('urs.earthdata.nasa.gov')
# print(username)


In [3]:
# import xarray as xr

# url = 'dap4://goldsmr4.gesdisc.eosdis.nasa.gov/opendap/MERRA2/M2T1NXSLV.5.12.4/2021/01/MERRA2_400.tavg1_2d_slv_Nx.20210101.nc4'


# ds = xr.open_dataset(url, decode_times=True, engine='pydap')
# print(list(ds.data_vars))    # List available variables
# print(ds)                   # Dataset info


# # Example: Print details for surface temperature (T2M), adjust for other variables as needed
# if 'T2M' in ds.data_vars:
#     print(ds['T2M'])
# else:
#     print("Variable 'T2M' not found. Available variables are:", list(ds.data_vars))

# # Example of subsetting: select January 1–5, latitudes 10–30N, longitudes 80–90E
# # Uncomment to use for spatiotemporal subsetting
# # subset = ds['T2M'].sel(time=slice('2021-01-01', '2021-01-05'), lat=slice(10, 30), lon=slice(80, 90))
# # print(subset)


In [4]:
# import xarray as xr
# import pandas as pd
# import numpy as np
# import os

# # Load AOIs from your Stations.csv
# stations = pd.read_csv('Stations.csv')

# # Define date range and days per month (no leap year)
# years = [2021, 2022]
# months = range(1, 13)
# days_per_month = {
#     1: 31, 2: 28, 3: 31, 4: 30, 5: 31, 6: 30,
#     7: 31, 8: 31, 9: 30, 10: 31, 11: 30, 12: 31
# }

# for idx, row in stations.iterrows():
#     for year in years:
#         for month in months:
#             for day in range(1, days_per_month[month] + 1):
#                 fname = f"MERRA2_400.tavg1_2d_slv_Nx.{year}{month:02d}{day:02d}.nc4"
#                 url = (
#                     f"https://goldsmr4.gesdisc.eosdis.nasa.gov/opendap/MERRA2/M2T1NXSLV.5.12.4/"
#                     f"{year}/{month:02d}/{fname}"
#                 )
#                 try:
#                     ds = xr.open_dataset(url, decode_times=True, engine='pydap')
#                     subset = ds.sel(
#                         lat=slice(row['south_lat'], row['north_lat']),
#                         lon=slice(row['west_lon'], row['east_lon'])
#                     )
#                     # Take mean over the subset area (can expand to other vars as needed)
#                     mean_val = float(subset['T2M'].mean().values) if 'T2M' in subset.data_vars else np.nan
#                     output = {
#                         "file_name": row['file_name'],
#                         "station_location": row['station_location'],
#                         "latitude": row['latitude'],
#                         "longitude": row['longitude'],
#                         "west_lon": row['west_lon'],
#                         "east_lon": row['east_lon'],
#                         "south_lat": row['south_lat'],
#                         "north_lat": row['north_lat'],
#                         "year": year,
#                         "month": month,
#                         "day": day,
#                         "T2M_mean": mean_val
#                     }
#                     output_file = "merra2_subset_results.csv"
#                     if not os.path.exists(output_file):
#                         pd.DataFrame([output]).to_csv(output_file, index=False)
#                     else:
#                         pd.DataFrame([output]).to_csv(output_file, mode='a', index=False, header=False)
#                 except Exception as e:
#                     print(f"Failed to access {url}: {e}")



In [1]:
# import os
# import time
# import requests
# import pandas as pd
# from requests.auth import HTTPBasicAuth
# import netrc

# # ==============================
# # CONFIGURATION
# # ==============================
# stations_file = "Stations.csv"   # Path to your stations file
# output_folder = "MERRA-2/MERRA-2_data_raw"  # Output path you gave
# dataset_id = "M2T1NXAER_5.12.4"  # Hourly aerosol diagnostics
# subset_url = "https://goldsmr4.gesdisc.eosdis.nasa.gov/daac-bin/OTF/HTTP_services.cgi"

# # Variables needed for PM estimation
# variables = [
#     "TOTEXTTAU",  # Total AOD
#     "DUEXTTAU",   # Dust AOD
#     "SUEXTTAU",   # Sulfate AOD
#     "OCEXTTAU",   # Organic carbon AOD
#     "BCEXTTAU",   # Black carbon AOD
#     "SSEXTTAU"    # Sea salt AOD
# ]

# date_start = "2021-01-01T00:00:00"
# date_end   = "2022-12-31T23:59:59"

# # Load Earthdata credentials from _netrc (explicit path on Windows)
# netrc_path = r"C:\Users\admin\_netrc"
# user, _, passwd = netrc.netrc(netrc_path).authenticators("urs.earthdata.nasa.gov")
# auth = HTTPBasicAuth(user, passwd)

# # Make sure output directory exists
# os.makedirs(output_folder, exist_ok=True)

# # ==============================
# # FUNCTIONS
# # ==============================

# def submit_job(station_name, west, south, east, north):
#     """Submit a subset request for one station using bounding box and return job ID."""
#     params = {
#         "dataset": dataset_id,
#         "service": "SUBSET",
#         "format": "CSV",
#         "variables": ",".join(variables),
#         "bbox": f"{west},{south},{east},{north}",
#         "startTime": date_start,
#         "endTime": date_end
#     }
#     resp = requests.get(subset_url, params=params, auth=auth)
#     if resp.status_code != 200:
#         raise RuntimeError(f"Job submission failed for {station_name}: {resp.text}")
    
#     if "jobID=" not in resp.text:
#         raise RuntimeError(f"No jobID returned for {station_name}: {resp.text}")
    
#     job_id = resp.text.split("jobID=")[1].split("&")[0].strip()
#     return job_id

# def check_status(job_id):
#     """Check the status of a submitted job."""
#     status_url = f"{subset_url}?request=check&jobID={job_id}"
#     resp = requests.get(status_url, auth=auth)
#     return resp.text

# def download_result(job_id, station_name):
#     """Download the completed subset result into output_folder."""
#     result_url = f"{subset_url}?request=get&jobID={job_id}"
#     out_path = os.path.join(output_folder, f"{station_name}.csv")
#     with requests.get(result_url, stream=True, auth=auth) as r:
#         r.raise_for_status()
#         with open(out_path, "wb") as f:
#             for chunk in r.iter_content(chunk_size=8192):
#                 f.write(chunk)
#     return out_path

# # ==============================
# # MAIN SCRIPT
# # ==============================

# stations = pd.read_csv(stations_file)

# for idx, row in stations.iterrows():
#     station_name = row["file_name"]   # e.g., DL008
#     west = row["west_lon"]
#     east = row["east_lon"]
#     south = row["south_lat"]
#     north = row["north_lat"]

#     print(f"📤 Submitting job for {station_name} (bbox: {west}, {south}, {east}, {north})...")
#     job_id = submit_job(station_name, west, south, east, north)
    
#     # Poll until job is ready
#     while True:
#         status = check_status(job_id)
#         if "done" in status.lower():
#             print(f"✅ {station_name} ready, downloading...")
#             file_path = download_result(job_id, station_name)
#             print(f"   ↳ Saved to {file_path}")
#             break
#         elif "error" in status.lower():
#             print(f"❌ Error for {station_name}: {status}")
#             break
#         else:
#             print(f"⏳ {station_name}: still processing...")
#             time.sleep(30)  # wait 30 seconds before checking again


In [3]:
# import os
# import requests
# import boto3
# from botocore.session import get_session
# import xarray as xr
# import netrc

# # ==============================
# # CONFIGURATION
# # ==============================
# output_folder = "MERRA-2/MERRA-2_data_raw"
# bucket = "gesdisc-cumulus-prod-protected"
# prefix = "MERRA2/M2T1NXAER.5.12.4"
# date_years = ["2021", "2022"]  # Only these years
# keep_vars = ["TOTEXTTAU", "DUEXTTAU", "SUEXTTAU", "OCEXTTAU", "BCEXTTAU", "SSEXTTAU"]
# os.makedirs(output_folder, exist_ok=True)

# # NASA Earthdata credentials (_netrc should already be set up)

# # ==============================
# # FUNCTIONS
# # ==============================

# def get_nasa_token():
#     """
#     Get temporary AWS credentials from NASA Earthdata login using _netrc.
#     """
#     url = "https://archive.gesdisc.eosdis.nasa.gov/s3credentials"
#     # Hardcode your Windows _netrc path
#     netrc_path = r"C:\Users\admin\_netrc"
#     info = netrc.netrc(netrc_path)
#     auth_data = info.authenticators("archive.gesdisc.eosdis.nasa.gov")
#     if auth_data is None:
#         raise RuntimeError("No _netrc entry for archive.gesdisc.eosdis.nasa.gov")
    
#     username, _, password = auth_data
#     r = requests.get(url, auth=requests.auth.HTTPBasicAuth(username, password))
#     r.raise_for_status()
#     return r.json()


# def s3_client_with_creds(creds):
#     """
#     Return a boto3 S3 client using NASA temporary credentials.
#     """
#     session = get_session()
#     s3 = session.create_client(
#         "s3",
#         region_name="us-east-1",
#         aws_access_key_id=creds["accessKeyId"],
#         aws_secret_access_key=creds["secretAccessKey"],
#         aws_session_token=creds["sessionToken"],
#     )
#     return s3

# def download_merra2_files():
#     creds = get_nasa_token()
#     s3 = s3_client_with_creds(creds)
#     errors = []

#     for year in date_years:
#         prefix_path = f"{prefix}/{year}/"
#         paginator = s3.get_paginator("list_objects_v2")
#         for page in paginator.paginate(Bucket=bucket, Prefix=prefix_path):
#             for obj in page.get("Contents", []):
#                 key = obj["Key"]
#                 file_name = os.path.basename(key)
#                 out_path = os.path.join(output_folder, file_name)

#                 try:
#                     if not os.path.exists(out_path):
#                         print(f"⬇️ Downloading {file_name}...")
#                         s3.download_file(bucket, key, out_path)
#                     else:
#                         print(f"✅ Already exists: {file_name}")
#                 except Exception as e:
#                     print(f"❌ Error downloading {file_name}: {e}")
#                     errors.append((file_name, str(e)))

#     if errors:
#         print("\n⚠️ Some files failed to download:")
#         for fn, msg in errors:
#             print(f"{fn}: {msg}")
#     return errors

# def slim_nc_files():
#     """
#     Open each downloaded .nc file, keep only selected variables, save smaller file.
#     """
#     for file in os.listdir(output_folder):
#         if file.endswith(".nc4"):
#             file_path = os.path.join(output_folder, file)
#             try:
#                 ds = xr.open_dataset(file_path)
#                 # Keep only the relevant variables
#                 ds_slim = ds[keep_vars]
#                 slim_path = os.path.join(output_folder, f"slim_{file}")
#                 ds_slim.to_netcdf(slim_path, format="NETCDF4")
#                 ds.close()
#                 ds_slim.close()
#                 print(f"💾 Slimmed file saved: slim_{file}")
#             except Exception as e:
#                 print(f"❌ Error processing {file}: {e}")

# # ==============================
# # MAIN
# # ==============================
# errors = download_merra2_files()
# if not errors:
#     slim_nc_files()
# else:
#     print("⚠️ Fix download errors before slimming files.")


In [4]:
# import os
# import requests

# # ==============================
# # CONFIG
# # ==============================
# output_folder = r"MERRA-2/MERRA-2_data_raw"
# urls_file = r"subset_M2T1NXAER_5.12.4_20250904_150749_.txt"  # replace with your .txt file path
# username = "amitjoshi"               # replace
# password = "dN6m#AVRc^wzNkn"               # replace
# os.makedirs(output_folder, exist_ok=True)

# # ==============================
# # READ LINKS (skip first line)
# # ==============================
# with open(urls_file, "r") as f:
#     urls = [line.strip() for line in f.readlines()[1:] if line.strip()]

# # ==============================
# # DOWNLOAD FILES
# # ==============================
# for url in urls:
#     file_name = url.split("FILENAME=")[-1].split("&")[0].split("/")[-1]  # extract .nc4 filename
#     out_path = os.path.join(output_folder, file_name)

#     if os.path.exists(out_path):
#         print(f"✅ Already exists: {file_name}")
#         continue

#     try:
#         print(f"⬇️ Downloading {file_name}...")
#         with requests.get(url, auth=(username, password), stream=True) as r:
#             r.raise_for_status()
#             with open(out_path, "wb") as f_out:
#                 for chunk in r.iter_content(chunk_size=8192):
#                     f_out.write(chunk)
#         print(f"✅ Downloaded: {file_name}")
#     except Exception as e:
#         print(f"❌ Error downloading {file_name}: {e}")

# print("\nAll downloads attempted.")


⬇️ Downloading %2Fdata%2FMERRA2%2FM2T1NXAER.5.12.4%2F2021%2F01%2FMERRA2_400.tavg1_2d_aer_Nx.20210101.nc4...
❌ Error downloading %2Fdata%2FMERRA2%2FM2T1NXAER.5.12.4%2F2021%2F01%2FMERRA2_400.tavg1_2d_aer_Nx.20210101.nc4: 401 Client Error: Unauthorized for url: https://urs.earthdata.nasa.gov/oauth/authorize/?scope=uid&app_type=401&client_id=e2WVk8Pw6weeLUKZYOxvTQ&response_type=code&redirect_uri=https%3A%2F%2Fgoldsmr4.gesdisc.eosdis.nasa.gov%2Fdata-redirect&state=aHR0cHM6Ly9nb2xkc21yNC5nZXNkaXNjLmVvc2Rpcy5uYXNhLmdvdi9kYWFjLWJpbi9PVEYvSFRUUF9zZXJ2aWNlcy5jZ2k%2FRklMRU5BTUU9JTJGZGF0YSUyRk1FUlJBMiUyRk0yVDFOWEFFUi41LjEyLjQlMkYyMDIxJTJGMDElMkZNRVJSQTJfNDAwLnRhdmcxXzJkX2Flcl9OeC4yMDIxMDEwMS5uYzQmTEFCRUw9TUVSUkEyXzQwMC50YXZnMV8yZF9hZXJfTnguMjAyMTAxMDEuU1VCLm5jJkJCT1g9MjguNjI3JTJDNzcuMTQ4JTJDMjguNjQ3JTJDNzcuMTY4JlNIT1JUTkFNRT1NMlQxTlhBRVImREFUQVNFVF9WRVJTSU9OPTUuMTIuNCZTRVJWSUNFPUwzNFJTX01FUlJBMiZGT1JNQVQ9Ym1NMEx3JlZBUklBQkxFUz1CQ0VYVFRBVSUyQ0RVRVhUVEFVJTJDT0NFWFRUQVUlMkNTU0VYVFRBVSUyQ1NVRVhUVEFVJT

KeyboardInterrupt: 

In [9]:
import os
import requests
from urllib.parse import urlparse, parse_qs

USERNAME = "amitjoshi"  # Your Earthdata username
PASSWORD = "dN6m#AVRc^wzNkn"  # Your Earthdata password (consider .netrc for security)

OUTPUT_DIR = r"MERRA-2/MERRA-2_data_raw"
URLS_FILE = r"subset_M2T1NXAER_5.12.4_20250904_150749_.txt"

os.makedirs(OUTPUT_DIR, exist_ok=True)

def earthdata_login(session):
    login_url = "https://urs.earthdata.nasa.gov/login"
    payload = {"username": USERNAME, "password": PASSWORD}
    headers = {"User-Agent": "Mozilla/5.0"}

    # First GET to establish session cookies
    session.get(login_url, headers=headers)

    # POST credentials to login
    resp = session.post(login_url, data=payload, headers=headers)
    resp.raise_for_status()
    if "urs_user_email" not in session.cookies.get_dict():
        raise RuntimeError("Earthdata login failed: Check your credentials.")
    print("Earthdata login successful.")

def get_filename_from_url(url):
    parsed = urlparse(url)
    query_params = parse_qs(parsed.query)
    filename_list = query_params.get("FILENAME") or query_params.get("filename")
    if filename_list:
        return filename_list[0].split("/")[-1]
    # fallback to path segment or generic name
    return parsed.path.split("/")[-1] or "downloaded_file"

def get_direct_url(session, service_url):
    # Request without redirects to get the Location header for direct URL
    resp = session.get(service_url, allow_redirects=False)
    if resp.status_code in [301, 302, 303, 307, 308]:
        redirected_url = resp.headers.get("Location")
        if redirected_url:
            return redirected_url
    resp.raise_for_status()
    return service_url

def download_file(session, url, filepath):
    with session.get(url, stream=True) as r:
        r.raise_for_status()
        with open(filepath, "wb") as f:
            for chunk in r.iter_content(chunk_size=8192):
                if chunk:
                    f.write(chunk)

def main():
    with open(URLS_FILE, "r") as f:
        service_urls = [line.strip() for line in f.readlines()[1:] if line.strip()]

    session = requests.Session()
    
    try:
        earthdata_login(session)
    except Exception as e:
        print(f"Login failed: {e}")
        return

    for service_url in service_urls:
        try:
            direct_url = get_direct_url(session, service_url)
            file_name = get_filename_from_url(direct_url)
            out_path = os.path.join(OUTPUT_DIR, file_name)
            
            if os.path.exists(out_path):
                print(f"✅ Already exists: {file_name}")
                continue
            
            print(f"⬇️ Downloading file: {file_name}")
            download_file(session, direct_url, out_path)
            print(f"✅ Downloaded: {file_name}")
        except Exception as e:
            print(f"❌ Error downloading {service_url}: {e}")

if __name__ == "__main__":
    main()


Login failed: Earthdata login failed: Check your credentials.


In [2]:
import os
import requests
from urllib.parse import urlparse, parse_qs

# Update with your Earthdata username (not used directly in code, for reference)
USERNAME = "amitjoshi"

# Output directory for downloads
OUTPUT_DIR = r"MERRA-2/MERRA-2_data_raw/DL009_2021_2022"
URLS_FILE = r"subset_M2T1NXAER_5.12.4_20250904_150749_.txt"

# Ensure output directory exists
os.makedirs(OUTPUT_DIR, exist_ok=True)

def get_filename_from_url(url):
    parsed = urlparse(url)
    query_params = parse_qs(parsed.query)
    filename_list = query_params.get("FILENAME") or query_params.get("filename")
    if filename_list:
        return filename_list[0].split("/")[-1]
    return parsed.path.split("/")[-1] or "downloaded_file"

def get_direct_url(session, service_url):
    # Follow redirect manually to get final direct download URL
    resp = session.get(service_url, allow_redirects=False)
    if resp.status_code in [301, 302, 303, 307, 308]:
        redirected_url = resp.headers.get("Location")
        if redirected_url:
            return redirected_url
    resp.raise_for_status()
    return service_url

def download_file(session, url, filepath):
    with session.get(url, stream=True) as r:
        r.raise_for_status()
        with open(filepath, "wb") as f:
            for chunk in r.iter_content(chunk_size=8192):
                if chunk:
                    f.write(chunk)

def main():
    with open(URLS_FILE, "r") as f:
        service_urls_raw = [line.strip() for line in f.readlines()[1:] if line.strip()]

    # Replace 'archive.gesdisc.eosdis.nasa.gov' with 'goldsmr4.gesdisc.eosdis.nasa.gov' in URLs
    service_urls = []
    for url in service_urls_raw:
        updated_url = url.replace("archive.gesdisc.eosdis.nasa.gov", "goldsmr4.gesdisc.eosdis.nasa.gov")
        service_urls.append(updated_url)

    # Start a requests session; requests uses .netrc automatically for authentication
    session = requests.Session()

    for service_url in service_urls:
        try:
            direct_url = get_direct_url(session, service_url)
            file_name = get_filename_from_url(direct_url)
            out_path = os.path.join(OUTPUT_DIR, file_name)

            if os.path.exists(out_path):
                print(f"✅ Already exists: {file_name}")
                continue

            print(f"⬇️ Downloading: {file_name}")
            download_file(session, direct_url, out_path)
            print(f"✅ Downloaded: {file_name}")

        except Exception as e:
            print(f"❌ Error downloading {service_url}: {e}")

if __name__ == "__main__":
    main()


⬇️ Downloading: downloaded_file
✅ Downloaded: downloaded_file
⬇️ Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210102.nc4
✅ Downloaded: MERRA2_400.tavg1_2d_aer_Nx.20210102.nc4
⬇️ Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210103.nc4
✅ Downloaded: MERRA2_400.tavg1_2d_aer_Nx.20210103.nc4
⬇️ Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210104.nc4
✅ Downloaded: MERRA2_400.tavg1_2d_aer_Nx.20210104.nc4
⬇️ Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210105.nc4
✅ Downloaded: MERRA2_400.tavg1_2d_aer_Nx.20210105.nc4
⬇️ Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210106.nc4
✅ Downloaded: MERRA2_400.tavg1_2d_aer_Nx.20210106.nc4
⬇️ Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210107.nc4
✅ Downloaded: MERRA2_400.tavg1_2d_aer_Nx.20210107.nc4
⬇️ Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210108.nc4
✅ Downloaded: MERRA2_400.tavg1_2d_aer_Nx.20210108.nc4
⬇️ Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210109.nc4
✅ Downloaded: MERRA2_400.tavg1_2d_aer_Nx.20210109.nc4
⬇️ Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210110.nc4
✅ 

KeyboardInterrupt: 

In [ ]:
import os
import requests
from urllib.parse import urlparse, parse_qs
from concurrent.futures import ThreadPoolExecutor, as_completed

USERNAME = "amitjoshi"  # For reference only, auth handled by .netrc
OUTPUT_DIR = r"MERRA-2/MERRA-2_data_raw/DL009_2021_2022"
URLS_FILE = r"subset_M2T1NXAER_5.12.4_20250904_150749_.txt"
MAX_WORKERS = 3  # Number of parallel downloads

os.makedirs(OUTPUT_DIR, exist_ok=True)

def get_filename_from_url(url):
    parsed = urlparse(url)
    query_params = parse_qs(parsed.query)
    filename_list = query_params.get("FILENAME") or query_params.get("filename")
    if filename_list:
        filename = filename_list[0].split("/")[-1]
        return filename
    filename = parsed.path.split("/")[-1]
    if not filename:
        print(f"Warning: URL missing filename segment: {url}")
        filename = "downloaded_file"
    return filename


def get_direct_url(session, service_url):
    resp = session.get(service_url, allow_redirects=False)
    if resp.status_code in [301, 302, 303, 307, 308]:
        redirected_url = resp.headers.get("Location")
        if redirected_url:
            return redirected_url
    resp.raise_for_status()
    return service_url

def download_file(session, service_url):
    try:
        direct_url = get_direct_url(session, service_url)
        file_name = get_filename_from_url(direct_url)
        out_path = os.path.join(OUTPUT_DIR, file_name)

        if os.path.exists(out_path):
            print(f"✅ Already exists: {file_name}")
            return file_name, "skipped"

        print(f"⬇️ Downloading: {file_name}")
        with session.get(direct_url, stream=True) as r:
            r.raise_for_status()
            with open(out_path, "wb") as f:
                for chunk in r.iter_content(chunk_size=8192):
                    if chunk:
                        f.write(chunk)
        print(f"✅ Downloaded: {file_name}")
        return file_name, "downloaded"

    except Exception as e:
        print(f"❌ Error downloading {service_url}: {e}")
        return service_url, "error"

def main():
    with open(URLS_FILE, "r") as f:
        service_urls_raw = [line.strip() for line in f.readlines()[1:] if line.strip()]

    # Replace 'archive.gesdisc.eosdis.nasa.gov' with 'goldsmr4.gesdisc.eosdis.nasa.gov'
    service_urls = [url.replace("archive.gesdisc.eosdis.nasa.gov", "goldsmr4.gesdisc.eosdis.nasa.gov") for url in service_urls_raw]

    session = requests.Session()

    with ThreadPoolExecutor(max_workers=MAX_WORKERS) as executor:
        # Submit download tasks
        futures = {executor.submit(download_file, session, url): url for url in service_urls}

        for future in as_completed(futures):
            file_url = futures[future]
            try:
                file_name, status = future.result()
            except Exception as exc:
                print(f"❌ Exception during download {file_url}: {exc}")

if __name__ == "__main__":
    main()


✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file

✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exists: downloaded_file
✅ Already exi

In [ ]:
import os
import re
import requests
from urllib.parse import urlparse, parse_qs
from concurrent.futures import ThreadPoolExecutor, as_completed
import threading

USERNAME = "amitjoshi"  # For reference only, auth handled by .netrc
OUTPUT_DIR = r"MERRA-2/MERRA-2_data_raw/DL009_2021_2022"
URLS_FILE = r"subset_M2T1NXAER_5.12.4_20250904_150749_.txt"
MAX_WORKERS = 3  # Number of parallel downloads

os.makedirs(OUTPUT_DIR, exist_ok=True)

# Thread-safe counter for fallback filenames
fallback_counter = 0
counter_lock = threading.Lock()

def get_filename_from_headers(headers):
    content_disp = headers.get('Content-Disposition')
    if content_disp:
        filename_match = re.findall('filename="?([^\'";]+)"?', content_disp)
        if filename_match:
            return filename_match[0]
    return None

def get_filename_from_url(url):
    global fallback_counter
    parsed = urlparse(url)
    query_params = parse_qs(parsed.query)
    filename_list = query_params.get("FILENAME") or query_params.get("filename")
    if filename_list:
        return filename_list[0].split("/")[-1]
    path_name = parsed.path.split("/")[-1]
    if path_name:
        return path_name
    # Fallback: assign unique downloaded_file_<n>
    with counter_lock:
        fallback_counter += 1
        return f"downloaded_file_{fallback_counter}"

def get_direct_url(session, service_url):
    resp = session.get(service_url, allow_redirects=False)
    if resp.status_code in [301, 302, 303, 307, 308]:
        redirected_url = resp.headers.get("Location")
        if redirected_url:
            return redirected_url
    resp.raise_for_status()
    return service_url

def download_file(session, service_url):
    try:
        direct_url = get_direct_url(session, service_url)
        with session.get(direct_url, stream=True) as r:
            r.raise_for_status()
            file_name = get_filename_from_headers(r.headers)
            if not file_name:
                file_name = get_filename_from_url(direct_url)
            out_path = os.path.join(OUTPUT_DIR, file_name)
            if os.path.exists(out_path):
                print(f"Already exists: {file_name} skipped")
                return file_name, "skipped"
            print(f"Downloading: {file_name}")
            with open(out_path, "wb") as f:
                for chunk in r.iter_content(chunk_size=8192):
                    if chunk:
                        f.write(chunk)
            print(f"{file_name} download complete")
            return file_name, "downloaded"
    except Exception:
        return service_url, "error"

def main():
    with open(URLS_FILE, "r") as f:
        service_urls_raw = [line.strip() for line in f.readlines()[1:] if line.strip()]
    service_urls = [url.replace("archive.gesdisc.eosdis.nasa.gov", "goldsmr4.gesdisc.eosdis.nasa.gov") for url in service_urls_raw]

    session = requests.Session()
    with ThreadPoolExecutor(max_workers=MAX_WORKERS) as executor:
        futures = {executor.submit(download_file, session, url): url for url in service_urls}
        for future in as_completed(futures):
            try:
                future.result()
            except Exception:
                pass

if __name__ == "__main__":
    main()


Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210102.SUB.nc
Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210101.SUB.nc
Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210103.SUB.nc
MERRA2_400.tavg1_2d_aer_Nx.20210103.SUB.nc download complete
MERRA2_400.tavg1_2d_aer_Nx.20210102.SUB.nc download complete
MERRA2_400.tavg1_2d_aer_Nx.20210101.SUB.nc download complete
Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210106.SUB.nc
Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210104.SUB.nc
MERRA2_400.tavg1_2d_aer_Nx.20210106.SUB.nc download complete
Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210105.SUB.nc
MERRA2_400.tavg1_2d_aer_Nx.20210104.SUB.nc download complete
MERRA2_400.tavg1_2d_aer_Nx.20210105.SUB.nc download complete
Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210109.SUB.nc
Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210107.SUB.nc
Downloading: MERRA2_400.tavg1_2d_aer_Nx.20210108.SUB.nc
MERRA2_400.tavg1_2d_aer_Nx.20210109.SUB.nc download complete
MERRA2_400.tavg1_2d_aer_Nx.20210107.SUB.nc download complete
MERRA2_4

In [ ]:
# Main code
import os
import re
import sys
import requests
from urllib.parse import urlparse, parse_qs
from concurrent.futures import ThreadPoolExecutor, as_completed
import threading

USERNAME = "amitjoshi"  # For reference only, auth handled by .netrc
OUTPUT_DIR = r"MERRA-2/MERRA-2_data_raw/Delhi/DL011_2021_2022"
URLS_FILE = r"MERRA-2/MERRA-2_data_raw/Delhi/Delhi_txt/subset_M2T1NXAER_5.12.4_20250905_063138_DL011.txt"
MAX_WORKERS = 5  # Number of parallel downloads

os.makedirs(OUTPUT_DIR, exist_ok=True)

# Thread-safe counters
downloaded_count = 0
skipped_count = 0
error_count = 0
count_lock = threading.Lock()

# Thread-safe counter for fallback filenames
fallback_counter = 0
counter_lock = threading.Lock()

def get_filename_from_headers(headers):
    content_disp = headers.get('Content-Disposition')
    if content_disp:
        filename_match = re.findall('filename="?([^\'";]+)"?', content_disp)
        if filename_match:
            return filename_match[0]
    return None

def get_filename_from_url(url):
    global fallback_counter
    parsed = urlparse(url)
    query_params = parse_qs(parsed.query)
    filename_list = query_params.get("FILENAME") or query_params.get("filename")
    if filename_list:
        return filename_list[0].split("/")[-1]
    path_name = parsed.path.split("/")[-1]
    if path_name:
        return path_name
    # Fallback: assign unique downloaded_file_<n>
    with counter_lock:
        fallback_counter += 1
        return f"downloaded_file_{fallback_counter}"

def get_direct_url(session, service_url):
    resp = session.get(service_url, allow_redirects=False)
    if resp.status_code in [301, 302, 303, 307, 308]:
        redirected_url = resp.headers.get("Location")
        if redirected_url:
            return redirected_url
    resp.raise_for_status()
    return service_url

def print_status():
    with count_lock:
        msg = f"Downloaded: {downloaded_count} | Skipped: {skipped_count} | Errors: {error_count}"
    print(msg.ljust(60), end="\r", flush=True)

def download_file(session, service_url):
    global downloaded_count, skipped_count, error_count
    try:
        direct_url = get_direct_url(session, service_url)
        with session.get(direct_url, stream=True) as r:
            r.raise_for_status()
            file_name = get_filename_from_headers(r.headers)
            if not file_name:
                file_name = get_filename_from_url(direct_url)
            out_path = os.path.join(OUTPUT_DIR, file_name)
            if os.path.exists(out_path):
                with count_lock:
                    skipped_count += 1
                return file_name, "skipped"
            with open(out_path, "wb") as f:
                for chunk in r.iter_content(chunk_size=8192):
                    if chunk:
                        f.write(chunk)
            with count_lock:
                downloaded_count += 1
            return file_name, "downloaded"
    except Exception as e:
        with count_lock:
            error_count += 1
        print(f"\nError downloading {service_url}: {e}")
        return service_url, "error"

def main():
    with open(URLS_FILE, "r") as f:
        service_urls_raw = [line.strip() for line in f.readlines()[1:] if line.strip()]
    service_urls = [url.replace("archive.gesdisc.eosdis.nasa.gov", "goldsmr4.gesdisc.eosdis.nasa.gov") for url in service_urls_raw]

    session = requests.Session()
    with ThreadPoolExecutor(max_workers=MAX_WORKERS) as executor:
        futures = {executor.submit(download_file, session, url): url for url in service_urls}
        for future in as_completed(futures):
            try:
                future.result()
            except Exception as exc:
                with count_lock:
                    global error_count
                    error_count += 1
                print(f"\nException during download: {exc}")
            print_status()
    print()  # Newline to finalize status line
    print(f"Download complete. Total: {len(service_urls)} | Downloaded: {downloaded_count} | Skipped: {skipped_count} | Errors: {error_count}")

if __name__ == "__main__":
    main()


Downloaded: 0 | Skipped: 284 | Errors: 0                    
Error downloading https://goldsmr4.gesdisc.eosdis.nasa.gov/daac-bin/OTF/HTTP_services.cgi?FILENAME=%2Fdata%2FMERRA2%2FM2T1NXAER.5.12.4%2F2021%2F10%2FMERRA2_400.tavg1_2d_aer_Nx.20211014.nc4&LABEL=MERRA2_400.tavg1_2d_aer_Nx.20211014.SUB.nc&VERSION=1.02&SERVICE=L34RS_MERRA2&SHORTNAME=M2T1NXAER&DATASET_VERSION=5.12.4&VARIABLES=BCEXTTAU%2CDUEXTTAU%2COCEXTTAU%2CSSEXTTAU%2CSUEXTTAU%2CTOTEXTTAU&FORMAT=bmM0Lw&BBOX=28.45%2C77.136%2C28.47%2C77.156: HTTPSConnectionPool(host='goldsmr4.gesdisc.eosdis.nasa.gov', port=443): Max retries exceeded with url: /daac-bin/OTF/HTTP_services.cgi?FILENAME=%2Fdata%2FMERRA2%2FM2T1NXAER.5.12.4%2F2021%2F10%2FMERRA2_400.tavg1_2d_aer_Nx.20211014.nc4&LABEL=MERRA2_400.tavg1_2d_aer_Nx.20211014.SUB.nc&VERSION=1.02&SERVICE=L34RS_MERRA2&SHORTNAME=M2T1NXAER&DATASET_VERSION=5.12.4&VARIABLES=BCEXTTAU%2CDUEXTTAU%2COCEXTTAU%2CSSEXTTAU%2CSUEXTTAU%2CTOTEXTTAU&FORMAT=bmM0Lw&BBOX=28.45%2C77.136%2C28.47%2C77.156 (Caused by 

In [7]:
import re
import os
import sys

folder_path = r"MERRA-2/MERRA-2_data_raw/Karnataka/KA002_2021_2022"

date_pattern = re.compile(r'\.(\d{8})\.')

def extract_date(filename):
    match = date_pattern.search(filename)
    if match:
        return match.group(1)
    return None

files = os.listdir(folder_path)
files_with_date = 0
files_without_date = 0

for fname in files:
    date_str = extract_date(fname)
    if date_str:
        files_with_date += 1
    else:
        files_without_date += 1
    # Dynamic print with carriage return to overwrite line
    msg = f"Files processed: {files_with_date + files_without_date} | Dates found: {files_with_date} | Dates missing: {files_without_date}"
    print(msg.ljust(70), end='\r', flush=True)

print()  # Newline after loop finishes
print(f"Final counts -> Total files: {len(files)} | Dates found: {files_with_date} | Dates missing: {files_without_date}")


Files processed: 730 | Dates found: 730 | Dates missing: 0            
Final counts -> Total files: 730 | Dates found: 730 | Dates missing: 0


In [4]:
from netCDF4 import Dataset

ds = Dataset("MERRA-2/MERRA-2_data_raw/DL009_2021_2022/MERRA2_400.tavg1_2d_aer_Nx.20210101.SUB.nc")
print(ds.variables["time"][:])


[   0   60  120  180  240  300  360  420  480  540  600  660  720  780
  840  900  960 1020 1080 1140 1200 1260 1320 1380]


In [10]:
# Robust upgrade to main code
import os
import re
import sys
import time
import requests
from urllib.parse import urlparse, parse_qs
from concurrent.futures import ThreadPoolExecutor, as_completed
import threading

USERNAME = "amitjoshi"  # For reference only, auth handled by .netrc
OUTPUT_DIR = r"MERRA-2/MERRA-2_data_raw/Karnataka/KA018_2021_2022"
URLS_FILE = r"MERRA-2/MERRA-2_data_raw/Karnataka/Karnataka_txt/subset_M2T1NXAER_5.12.4_20250906_130902_KA018.txt"
MAX_WORKERS = 5  # Number of parallel downloads
TIMEOUT = 10  # seconds for HTTP request timeout
MAX_RETRIES = 3  # Number of retries per file

os.makedirs(OUTPUT_DIR, exist_ok=True)

# Thread-safe counters
downloaded_count = 0
skipped_count = 0
error_count = 0
count_lock = threading.Lock()

# Thread-safe counter for fallback filenames
fallback_counter = 0
counter_lock = threading.Lock()

def get_filename_from_headers(headers):
    content_disp = headers.get('Content-Disposition')
    if content_disp:
        filename_match = re.findall('filename="?([^\'";]+)"?', content_disp)
        if filename_match:
            return filename_match[0]
    return None

def get_filename_from_url(url):
    global fallback_counter
    parsed = urlparse(url)
    query_params = parse_qs(parsed.query)
    filename_list = query_params.get("FILENAME") or query_params.get("filename")
    if filename_list:
        return filename_list[0].split("/")[-1]
    path_name = parsed.path.split("/")[-1]
    if path_name:
        return path_name
    with counter_lock:
        fallback_counter += 1
        return f"downloaded_file_{fallback_counter}"

def get_direct_url(session, service_url):
    resp = session.get(service_url, allow_redirects=False, timeout=TIMEOUT)
    if resp.status_code in [301, 302, 303, 307, 308]:
        redirected_url = resp.headers.get("Location")
        if redirected_url:
            return redirected_url
    resp.raise_for_status()
    return service_url

def print_status():
    with count_lock:
        msg = f"Downloaded: {downloaded_count} | Skipped: {skipped_count} | Errors: {error_count}"
    print(msg.ljust(60), end="\r", flush=True)

def download_file(session, service_url, retries=MAX_RETRIES, timeout=TIMEOUT):
    global downloaded_count, skipped_count, error_count
    for attempt in range(1, retries + 1):
        try:
            direct_url = get_direct_url(session, service_url)
            with session.get(direct_url, stream=True, timeout=timeout) as r:
                r.raise_for_status()
                file_name = get_filename_from_headers(r.headers)
                if not file_name:
                    file_name = get_filename_from_url(direct_url)
                out_path = os.path.join(OUTPUT_DIR, file_name)
                if os.path.exists(out_path):
                    with count_lock:
                        skipped_count += 1
                    return file_name, "skipped"
                with open(out_path, "wb") as f:
                    for chunk in r.iter_content(chunk_size=8192):
                        if chunk:
                            f.write(chunk)
                with count_lock:
                    downloaded_count += 1
                return file_name, "downloaded"
        except Exception as e:
            if attempt == retries:
                with count_lock:
                    error_count += 1
                print(f"\nError downloading {service_url} after {attempt} attempts: {e}")
                return service_url, "error"
            else:
                wait_time = 2 ** attempt  # exponential backoff: 2, 4, 8 seconds
                print(f"\nAttempt {attempt} failed for {service_url}: {e}. Retrying in {wait_time}s...")
                time.sleep(wait_time)

def main():
    with open(URLS_FILE, "r") as f:
        service_urls_raw = [line.strip() for line in f.readlines()[1:] if line.strip()]
    # Replace archive URL with goldsmr4 URL as before
    service_urls = [url.replace("archive.gesdisc.eosdis.nasa.gov", "goldsmr4.gesdisc.eosdis.nasa.gov") for url in service_urls_raw]

    session = requests.Session()
    with ThreadPoolExecutor(max_workers=MAX_WORKERS) as executor:
        futures = {executor.submit(download_file, session, url): url for url in service_urls}
        for future in as_completed(futures):
            try:
                future.result()
            except Exception as exc:
                with count_lock:
                    global error_count
                    error_count += 1
                print(f"\nException during download: {exc}")
            print_status()
    print()  # Newline to finalize status line
    print(f"Download complete. Total: {len(service_urls)} | Downloaded: {downloaded_count} | Skipped: {skipped_count} | Errors: {error_count}")

if __name__ == "__main__":
    main()


Downloaded: 730 | Skipped: 0 | Errors: 0                    
Download complete. Total: 730 | Downloaded: 730 | Skipped: 0 | Errors: 0


In [1]:
import os
import time
from urllib.parse import urlparse, parse_qs

# Update these paths as needed
URLS_FILE = r"Delhi_txt/subset_M2T1NXAER_5.12.4_20250905_063138_DL011.txt"
OUTPUT_DIR = r"MERRA-2/MERRA-2_data_raw/DL011_2021_2022"

def get_filename_from_url(url):
    parsed = urlparse(url)
    query_params = parse_qs(parsed.query)
    filename_list = query_params.get("FILENAME") or query_params.get("filename")
    if filename_list:
        return filename_list[0].split("/")[-1]
    path_name = parsed.path.split("/")[-1]
    if path_name:
        return path_name
    return "downloaded_file"

def load_urls():
    with open(URLS_FILE, "r") as f:
        return [line.strip() for line in f.readlines()[1:] if line.strip()]

def benchmark_skip_logic():
    urls = load_urls()

    # Benchmark filename parsing
    start = time.time()
    filenames = [get_filename_from_url(url) for url in urls]
    end = time.time()
    print(f"Filename parsing for {len(urls)} URLs took {end - start:.4f} seconds")

    # Benchmark directory listing
    start = time.time()
    existing_files = set(os.listdir(OUTPUT_DIR))
    end = time.time()
    print(f"Directory listing took {end - start:.4f} seconds for {len(existing_files)} files")

    # Benchmark skip checks (membership test)
    start = time.time()
    skipped = sum(fname in existing_files for fname in filenames)
    end = time.time()
    print(f"Skip membership checks took {end - start:.4f} seconds, skipped {skipped} files")

if __name__ == "__main__":
    benchmark_skip_logic()


Filename parsing for 730 URLs took 0.0876 seconds
Directory listing took 0.0010 seconds for 315 files
Skip membership checks took 0.0000 seconds, skipped 0 files


In [ ]:
# Second Optimization of main code
import os
import re
import sys
import time
import requests
from urllib.parse import urlparse, parse_qs
from concurrent.futures import ThreadPoolExecutor, as_completed
import threading

USERNAME = "amitjoshi"  # For reference only, auth handled by .netrc
OUTPUT_DIR = r"MERRA-2/MERRA-2_data_raw/DL011_2021_2022"
URLS_FILE = r"Delhi_txt/subset_M2T1NXAER_5.12.4_20250905_063138_DL011.txt"
MAX_WORKERS = 5  # Number of parallel downloads

os.makedirs(OUTPUT_DIR, exist_ok=True)

# Thread-safe counters
downloaded_count = 0
skipped_count = 0
error_count = 0
count_lock = threading.Lock()

# Thread-safe counter for fallback filenames
fallback_counter = 0
counter_lock = threading.Lock()

def get_filename_from_headers(headers):
    content_disp = headers.get('Content-Disposition')
    if content_disp:
        filename_match = re.findall('filename="?([^\'";]+)"?', content_disp)
        if filename_match:
            return filename_match[0]
    return None

def get_filename_from_url(url):
    global fallback_counter
    parsed = urlparse(url)
    query_params = parse_qs(parsed.query)
    filename_list = query_params.get("FILENAME") or query_params.get("filename")
    if filename_list:
        return filename_list[0].split("/")[-1]
    path_name = parsed.path.split("/")[-1]
    if path_name:
        return path_name
    with counter_lock:
        fallback_counter += 1
        return f"downloaded_file_{fallback_counter}"

def get_direct_url(session, service_url):
    resp = session.get(service_url, allow_redirects=False)
    if resp.status_code in [301, 302, 303, 307, 308]:
        redirected_url = resp.headers.get("Location")
        if redirected_url:
            return redirected_url
    resp.raise_for_status()
    return service_url

def print_status():
    with count_lock:
        msg = f"Downloaded: {downloaded_count} | Skipped: {skipped_count} | Errors: {error_count}"
    print(msg.ljust(60), end="\r", flush=True)

def download_file(session, service_url, out_path):
    global downloaded_count, skipped_count, error_count
    try:
        start_total = time.time()

        # Time URL redirection resolution
        start_redirect = time.time()
        direct_url = get_direct_url(session, service_url)
        end_redirect = time.time()

        with session.get(direct_url, stream=True) as r:
            r.raise_for_status()

            # Time filename extraction from headers
            start_fname = time.time()
            file_name = get_filename_from_headers(r.headers)
            end_fname = time.time()

            if file_name:
                updated_out_path = os.path.join(OUTPUT_DIR, file_name)
            else:
                updated_out_path = out_path

            # Skip file check
            if os.path.exists(updated_out_path):
                with count_lock:
                    skipped_count += 1
                return file_name or os.path.basename(updated_out_path), "skipped"

            # Time actual download
            start_download = time.time()
            with open(updated_out_path, "wb") as f:
                for chunk in r.iter_content(chunk_size=8192):
                    if chunk:
                        f.write(chunk)
            end_download = time.time()

        with count_lock:
            downloaded_count += 1

        end_total = time.time()

        print(
            f"\nFile: {os.path.basename(updated_out_path)} | "
            f"Redirect: {end_redirect - start_redirect:.2f}s | "
            f"Filename header extraction: {end_fname - start_fname:.4f}s | "
            f"Download: {end_download - start_download:.2f}s | "
            f"Total: {end_total - start_total:.2f}s"
        )

        return file_name or os.path.basename(updated_out_path), "downloaded"
    except Exception as e:
        with count_lock:
            error_count += 1
        print(f"\nError downloading {service_url}: {e}")
        return service_url, "error"

def main():
    global skipped_count
    with open(URLS_FILE, "r") as f:
        service_urls_raw = [line.strip() for line in f.readlines()[1:] if line.strip()]
    service_urls = [url.replace("archive.gesdisc.eosdis.nasa.gov", "goldsmr4.gesdisc.eosdis.nasa.gov") for url in service_urls_raw]

    existing_files = set(os.listdir(OUTPUT_DIR))

    to_download = []
    skipped_count = 0
    for url in service_urls:
        file_name = get_filename_from_url(url)
        if file_name in existing_files:
            skipped_count += 1
        else:
            out_path = os.path.join(OUTPUT_DIR, file_name)
            to_download.append((url, out_path))

    session = requests.Session()
    with ThreadPoolExecutor(max_workers=MAX_WORKERS) as executor:
        futures = {executor.submit(download_file, session, url, out_path): url for url, out_path in to_download}
        for future in as_completed(futures):
            try:
                future.result()
            except Exception as exc:
                with count_lock:
                    global error_count
                    error_count += 1
                print(f"\nException during download: {exc}")
            print_status()
    print()  # Newline to finalize status line
    print(f"Download complete. Total: {len(service_urls)} | Downloaded: {downloaded_count} | Skipped: {skipped_count} | Errors: {error_count}")

if __name__ == "__main__":
    main()


Downloaded: 0 | Skipped: 35 | Errors: 0                     

In [2]:
from netCDF4 import Dataset

# Open NetCDF file
with Dataset("MERRA-2/MERRA-2_data_raw/Haryana/HR001_2021_2022/MERRA2_400.tavg1_2d_aer_Nx.20210101.SUB.nc", "r") as ds:
    print("Dimensions:", ds.dimensions.keys())
    print("Variables:", ds.variables.keys())

    # Example: read a variable
    var_data = ds.variables['TOTEXTTAU'][:]
print(var_data)


Dimensions: dict_keys(['time', 'lon', 'lat'])
Variables: dict_keys(['time', 'lon', 'lat', 'BCEXTTAU', 'DUEXTTAU', 'OCEXTTAU', 'SSEXTTAU', 'SUEXTTAU', 'TOTEXTTAU'])
[[[0.32892728]]

 [[0.30880883]]

 [[0.2902651 ]]

 [[0.27697456]]

 [[0.2722484 ]]

 [[0.27375185]]

 [[0.5884386 ]]

 [[0.59444433]]

 [[0.59742975]]

 [[0.59817994]]

 [[0.62503564]]

 [[0.6724446 ]]

 [[0.7469778 ]]

 [[0.83834165]]

 [[0.9208724 ]]

 [[1.0060514 ]]

 [[1.0655726 ]]

 [[1.0855362 ]]

 [[1.1338308 ]]

 [[1.26808   ]]

 [[1.4775312 ]]

 [[1.6537553 ]]

 [[1.7255204 ]]

 [[1.7904725 ]]]


In [3]:
with Dataset("MERRA-2/MERRA-2_data_raw/Haryana/HR001_2021_2022/MERRA2_400.tavg1_2d_aer_Nx.20210101.SUB.nc", "r") as ds:
    for dim in ds.dimensions:
        print(f"Dimension {dim}: size {len(ds.dimensions[dim])}")


Dimension time: size 24
Dimension lon: size 1
Dimension lat: size 1


In [6]:
nc_file = "MERRA-2/MERRA-2_data_raw/Haryana/HR001_2021_2022/MERRA2_400.tavg1_2d_aer_Nx.20210101.SUB.nc"
def check_file_completeness_single_point(nc_file_path, west, south, east, north, epsilon=0.03):
    try:
        with Dataset(nc_file_path, "r") as ds:
            if len(ds.dimensions['time']) != 24:
                return False, f"Unexpected time size: {len(ds.dimensions['time'])}, expected 24"
            if len(ds.dimensions['lat']) != 1 or len(ds.dimensions['lon']) != 1:
                return False, f"Spatial dimension size unexpected: lat {len(ds.dimensions['lat'])}, lon {len(ds.dimensions['lon'])}"

            lon = ds.variables['lon'][0]
            lat = ds.variables['lat'][0]

            if not (west - epsilon <= lon <= east + epsilon):
                return False, f"Longitude {lon} outside bounds {west} to {east} (+/- {epsilon})"
            if not (south - epsilon <= lat <= north + epsilon):
                return False, f"Latitude {lat} outside bounds {south} to {north} (+/- {epsilon})"

            for var_name in REQUIRED_VARS:
                if var_name not in ds.variables:
                    return False, f"Missing variable: {var_name}"
                var = ds.variables[var_name]
                if var.shape != (24, 1, 1):
                    return False, f"Variable {var_name} shape {var.shape} unexpected, expected (24,1,1)"

        return True, "File structure and data look complete"
    except Exception as e:
        return False, f"Error reading file: {e}"

check_file_completeness_single_point(nc_file, 77.309, 28.395, 77.329, 28.415)



(False, 'Longitude 77.5 outside bounds 77.309 to 77.329 (+/- 0.03)')

In [7]:
# from netCDF4 import Dataset
# import numpy as np

# def check_variable_data(nc_file_path, required_vars):
#     try:
#         with Dataset(nc_file_path, "r") as ds:
#             results = {}
#             for var_name in required_vars:
#                 if var_name not in ds.variables:
#                     results[var_name] = "Missing"
#                     continue
                
#                 var = ds.variables[var_name]
#                 data = var[:]
#                 fill_val = getattr(var, '_FillValue', None)

#                 # Count missing values if fill value exists
#                 if fill_val is not None:
#                     missing_count = np.sum(data == fill_val)
#                 else:
#                     missing_count = 0

#                 # Count total data points
#                 total_count = data.size

#                 # Basic stats (min, max)
#                 valid_data = data[data != fill_val] if fill_val is not None else data
#                 data_min = np.min(valid_data)
#                 data_max = np.max(valid_data)

#                 results[var_name] = {
#                     'shape': var.shape,
#                     'total_points': total_count,
#                     'missing_points': missing_count,
#                     'min_value': data_min,
#                     'max_value': data_max
#                 }
#         return results
#     except Exception as e:
#         return f"Error reading file: {e}"

# # Example usage
# nc_file = "MERRA-2/MERRA-2_data_raw/Haryana/HR001_2021_2022/MERRA2_400.tavg1_2d_aer_Nx.20210101.SUB.nc"
# required_vars = ['BCEXTTAU', 'DUEXTTAU', 'OCEXTTAU', 'SSEXTTAU', 'SUEXTTAU', 'TOTEXTTAU']
# var_stats = check_variable_data(nc_file, required_vars)
# print(var_stats)


{'BCEXTTAU': {'shape': (24, 1, 1), 'total_points': 24, 'missing_points': 0, 'min_value': 0.04358502, 'max_value': 0.15762864}, 'DUEXTTAU': {'shape': (24, 1, 1), 'total_points': 24, 'missing_points': 0, 'min_value': 0.013775806, 'max_value': 0.0238511}, 'OCEXTTAU': {'shape': (24, 1, 1), 'total_points': 24, 'missing_points': 0, 'min_value': 0.06519869, 'max_value': 0.4972267}, 'SSEXTTAU': {'shape': (24, 1, 1), 'total_points': 24, 'missing_points': 0, 'min_value': 0.0014959789, 'max_value': 0.0082565695}, 'SUEXTTAU': {'shape': (24, 1, 1), 'total_points': 24, 'missing_points': 0, 'min_value': 0.13614805, 'max_value': 1.1054155}, 'TOTEXTTAU': {'shape': (24, 1, 1), 'total_points': 24, 'missing_points': 0, 'min_value': 0.2722484, 'max_value': 1.7904725}}


In [11]:
# import os
# import csv
# from netCDF4 import Dataset

# CSV_FILE = "Stations_MERRA-2.csv"
# BASE_DATA_DIR = "MERRA-2/MERRA-2_data_raw"

# REQUIRED_VARS = ['BCEXTTAU', 'DUEXTTAU', 'OCEXTTAU', 'SSEXTTAU', 'SUEXTTAU', 'TOTEXTTAU']

# def check_file_completeness_single_point(nc_file_path, west, south, east, north, required_vars=REQUIRED_VARS, epsilon=0.03):
#     try:
#         with Dataset(nc_file_path, "r") as ds:
#             if len(ds.dimensions['time']) != 24:
#                 return False, f"Unexpected time size: {len(ds.dimensions['time'])}, expected 24"
#             if len(ds.dimensions['lat']) != 1 or len(ds.dimensions['lon']) != 1:
#                 return False, f"Spatial dimension size unexpected: lat {len(ds.dimensions['lat'])}, lon {len(ds.dimensions['lon'])}"
#             lon = ds.variables['lon'][0]
#             lat = ds.variables['lat'][0]
#             if not (west - epsilon <= lon <= east + epsilon):
#                 return False, f"Longitude {lon} outside bounds {west}–{east} (+/- {epsilon})"
#             if not (south - epsilon <= lat <= north + epsilon):
#                 return False, f"Latitude {lat} outside bounds {south}–{north} (+/- {epsilon})"
#             for var_name in required_vars:
#                 if var_name not in ds.variables:
#                     return False, f"Missing variable: {var_name}"
#                 var = ds.variables[var_name]
#                 if var.shape != (24, 1, 1):
#                     return False, f"Variable {var_name} shape {var.shape} unexpected, expected (24,1,1)"
#         return True, "File structure and data look complete"
#     except Exception as e:
#         return False, f"Error reading file: {e}"

# def main():
#     with open(CSV_FILE, newline='', encoding='utf-8-sig') as stations_csv:
#         reader = list(csv.DictReader(stations_csv))
        
#         # Find index of HR001
#         start_index = next((i for i, row in enumerate(reader) if row['file_name'] == "HR001"), None)
#         if start_index is None:
#             print("HR001 station not found in CSV.")
#             return
        
#         # Process 5 consecutive Haryana stations
#         haryana_stations = reader[start_index : start_index + 5]

#         for row in haryana_stations:
#             file_prefix = row['file_name']
#             west = float(row['west_lon'])
#             south = float(row['south_lat'])
#             east = float(row['east_lon'])
#             north = float(row['north_lat'])
#             folder = os.path.join(BASE_DATA_DIR, "Haryana", file_prefix + "_2021_2022")

#             if not os.path.isdir(folder):
#                 print(f"[SKIP] Folder not found for station: {file_prefix}")
#                 continue

#             nc_files = sorted([f for f in os.listdir(folder) if f.endswith(".nc")])
#             if not nc_files:
#                 print(f"[SKIP] No .nc files for station: {file_prefix}")
#                 continue

#             first_nc = nc_files[0]
#             nc_file_path = os.path.join(folder, first_nc)
#             status, message = check_file_completeness_single_point(
#                 nc_file_path, west, south, east, north, REQUIRED_VARS
#             )
#             print(f"Station: {file_prefix} | File: {first_nc} | Status: {message}")

# if __name__ == "__main__":
#     main()


Station: HR001 | File: MERRA2_400.tavg1_2d_aer_Nx.20210101.SUB.nc | Status: Longitude 77.5 outside bounds 77.309–77.329 (+/- 0.03)
Station: HR002 | File: MERRA2_400.tavg1_2d_aer_Nx.20210101.SUB.nc | Status: Longitude 76.875 outside bounds 77.016–77.036 (+/- 0.03)
Station: HR003 | File: MERRA2_400.tavg1_2d_aer_Nx.20210101.SUB.nc | Status: File structure and data look complete
Station: HR004 | File: MERRA2_400.tavg1_2d_aer_Nx.20210101.SUB.nc | Status: Longitude 76.875 outside bounds 76.584–76.604 (+/- 0.03)
Station: HR009 | File: MERRA2_400.tavg1_2d_aer_Nx.20210101.SUB.nc | Status: Longitude 76.25 outside bounds 76.307–76.327 (+/- 0.03)


In [4]:
# .nc to csv trial 
import os
import re
import sys
import pandas as pd
import xarray as xr

# ========== CONFIG ==========
RAW_BASE_DIR = "MERRA-2/MERRA-2_data_raw"
PROCESSED_BASE_DIR = "MERRA-2/MERRA-2_data_processed1"
# Set a specific file to process, else the script auto-finds the first .nc
TEST_NC_PATH = r"C:\Users\admin\Desktop\Corrupted_recheck\MERRA2_401.tavg1_2d_aer_Nx.20210818.SUB.nc"
# Only these six PM-related aerosol variables
VARS = ["BCEXTTAU", "DUEXTTAU", "OCEXTTAU", "SSEXTTAU", "SUEXTTAU", "TOTEXTTAU"]
REQUIRED_TIME_ROWS = 24
# ===========================

def ensure_dir(path: str):
    os.makedirs(path, exist_ok=True)

def find_first_nc(root: str):
    # Walk two levels: state -> station; skip *_txt folders
    for state in sorted(os.listdir(root)):
        state_path = os.path.join(root, state)
        if not os.path.isdir(state_path):
            continue
        if state.lower() == "state_txt" or state.lower().endswith("_txt"):
            continue
        for sub in sorted(os.listdir(state_path)):
            sub_path = os.path.join(state_path, sub)
            if not os.path.isdir(sub_path):
                continue
            if sub.lower() == "state_txt" or sub.lower().endswith("_txt"):
                continue
            for fname in sorted(os.listdir(sub_path)):
                if fname.endswith(".nc"):
                    return os.path.join(sub_path, fname)
    return None

def derive_station_code(nc_path: str) -> str:
    # Parent folder like "DL009_2021_2022" -> take first 5 chars "DL009"
    station_folder = os.path.basename(os.path.dirname(os.fspath(nc_path)))
    return station_folder[:5]

def extract_date_from_filename(nc_path: str) -> str:
    # Extract YYYYMMDD from NetCDF filename
    fname = os.path.basename(os.fspath(nc_path))
    m = re.search(r"\d{8}", fname)
    if not m:
        raise ValueError(f"Could not find 8-digit date in filename: {fname}")
    return m.group(0)

def out_csv_path(nc_path: str, station_code: str, date_str: str) -> str:
    # Output under processed mirror: processed/<state>/<station_folder>/<Stationcode_YYYYMMDD_C1_full.csv>
    station_path = os.path.dirname(os.fspath(nc_path))
    state_path = os.path.dirname(station_path)
    state = os.path.basename(state_path)
    station_folder = os.path.basename(station_path)
    out_name = f"{station_code}_{date_str}_C1_full.csv"
    return os.path.join(PROCESSED_BASE_DIR, state, station_folder, out_name)

def convert_nc_to_df(nc_path: str) -> pd.DataFrame:
    ds = xr.open_dataset(nc_path, decode_times=True)
    present = [v for v in VARS if v in ds.data_vars]
    if not present:
        raise ValueError(f"No requested variables present in {os.path.basename(nc_path)}; looked for {VARS}")
    # Flatten variables to columns; coordinates (time, lat, lon) come via index and reset to columns
    df = ds[present].to_dataframe().reset_index()
    # Normalize time, derive hourly label, and format without seconds
    df["time"] = pd.to_datetime(df["time"], utc=True)
    df["hour_utc"] = df["time"].dt.hour
    df["time_utc"] = df["time"].dt.strftime("%Y-%m-%d %H:%M")
    # Build final schema: station_code + time_utc + hour_utc + six variables
    station_code = derive_station_code(nc_path)
    n = len(df)
    out = pd.DataFrame({
        "station_code": [station_code] * n,   # broadcast scalar DL009
        "time_utc": df["time_utc"],
        "hour_utc": df["hour_utc"],
    })
    for v in VARS:
        out[v] = df[v] if v in df.columns else pd.NA
    return out

def basic_validate(df: pd.DataFrame):
    if "station_code" not in df.columns:
        return False, "Missing station_code column"
    if "time_utc" not in df.columns or "hour_utc" not in df.columns:
        return False, "Missing time_utc/hour_utc columns"
    if len(df) != REQUIRED_TIME_ROWS:
        return False, f"Unexpected rows: {len(df)} != {REQUIRED_TIME_ROWS}"
    for v in VARS:
        if v not in df.columns:
            return False, f"Missing variable column: {v}"
    return True, "OK"

def main():
    ensure_dir(PROCESSED_BASE_DIR)
    test_path = TEST_NC_PATH or find_first_nc(RAW_BASE_DIR)
    if not test_path:
        print("No .nc files found to process under RAW_BASE_DIR; aborting.")
        sys.exit(1)
    try:
        print(f"[ONE] Converting single file: {test_path}")
        df = convert_nc_to_df(test_path)
        ok, msg = basic_validate(df)
        print(f"[ONE] Validation: {msg}")
        station_code = derive_station_code(test_path)
        date_str = extract_date_from_filename(test_path)
        out_csv = out_csv_path(test_path, station_code, date_str)
        ensure_dir(os.path.dirname(out_csv))
        df.to_csv(out_csv, index=False)
        print(f"[ONE] Wrote: {out_csv}")
    except Exception as e:
        print(f"[ONE-FAIL] {e}")
        sys.exit(2)

if __name__ == "__main__":
    main()


[ONE] Converting single file: C:\Users\admin\Desktop\Corrupted_recheck\MERRA2_401.tavg1_2d_aer_Nx.20210818.SUB.nc
[ONE] Validation: OK
[ONE] Wrote: MERRA-2/MERRA-2_data_processed1\Desktop\Corrupted_recheck\Corru_20210818_C1_full.csv


In [28]:
# # .nc to csv actual (bulk)
# import os
# import re
# import sys
# import pandas as pd
# import xarray as xr

# # ========== CONFIG ==========
# RAW_BASE_DIR = "MERRA-2/MERRA-2_data_raw"             # root with state/station folders
# PROCESSED_BASE_DIR = "MERRA-2/MERRA-2_data_processed"  # output mirror
# VARS = ["BCEXTTAU", "DUEXTTAU", "OCEXTTAU", "SSEXTTAU", "SUEXTTAU", "TOTEXTTAU"]
# REQUIRED_TIME_ROWS = 24
# SKIP_DIR_SUFFIX = "_txt"
# SKIP_DIR_EXACT = "state_txt"
# # ===========================

# def ensure_dir(path: str):
#     os.makedirs(path, exist_ok=True)

# def derive_station_code(nc_path: str) -> str:
#     # Parent folder like "DL009_2021_2022" -> "DL009"
#     station_folder = os.path.basename(os.path.dirname(os.fspath(nc_path)))
#     return station_folder[:5]

# def extract_date_from_filename(nc_path: str) -> str:
#     # Extract YYYYMMDD from NetCDF filename
#     fname = os.path.basename(os.fspath(nc_path))
#     m = re.search(r"\d{8}", fname)
#     if not m:
#         raise ValueError(f"Could not find 8-digit date in filename: {fname}")
#     return m.group(0)

# def out_csv_path(nc_path: str, station_code: str, date_str: str) -> str:
#     # processed/<state>/<station_folder>/<Stationcode_YYYYMMDD_C1_full.csv>
#     station_path = os.path.dirname(os.fspath(nc_path))
#     state_path = os.path.dirname(station_path)
#     state = os.path.basename(state_path)
#     station_folder = os.path.basename(station_path)
#     out_name = f"{station_code}_{date_str}_C1_full.csv"
#     return os.path.join(PROCESSED_BASE_DIR, state, station_folder, out_name)

# def convert_nc_to_df(nc_path: str) -> pd.DataFrame:
#     ds = xr.open_dataset(nc_path, decode_times=True)
#     present = [v for v in VARS if v in ds.data_vars]
#     if not present:
#         raise ValueError(f"No requested variables present in {os.path.basename(nc_path)}; looked for {VARS}")
#     df = ds[present].to_dataframe().reset_index()
#     df["time"] = pd.to_datetime(df["time"], utc=True)
#     df["hour_utc"] = df["time"].dt.hour
#     df["time_utc"] = df["time"].dt.strftime("%Y-%m-%d %H:%M")
#     station_code = derive_station_code(nc_path)
#     n = len(df)
#     out = pd.DataFrame({
#         "station_code": [station_code] * n,
#         "time_utc": df["time_utc"],
#         "hour_utc": df["hour_utc"],
#     })
#     for v in VARS:
#         out[v] = df[v] if v in df.columns else pd.NA
#     return out

# def basic_validate(df: pd.DataFrame):
#     if "station_code" not in df.columns:
#         return False, "Missing station_code column"
#     if "time_utc" not in df.columns or "hour_utc" not in df.columns:
#         return False, "Missing time_utc/hour_utc columns"
#     if len(df) != REQUIRED_TIME_ROWS:
#         return False, f"Unexpected rows: {len(df)} != {REQUIRED_TIME_ROWS}"
#     for v in VARS:
#         if v not in df.columns:
#             return False, f"Missing variable column: {v}"
#     return True, "OK"

# def should_skip_dir(name: str) -> bool:
#     lname = name.lower()
#     return lname == SKIP_DIR_EXACT or lname.endswith(SKIP_DIR_SUFFIX)

# def process_all():
#     for state in sorted(os.listdir(RAW_BASE_DIR)):
#         state_path = os.path.join(RAW_BASE_DIR, state)
#         if not os.path.isdir(state_path) or should_skip_dir(state):
#             continue
#         for station in sorted(os.listdir(state_path)):
#             station_path = os.path.join(state_path, station)
#             if not os.path.isdir(station_path) or should_skip_dir(station):
#                 continue
#             for fname in sorted(os.listdir(station_path)):
#                 if not fname.endswith(".nc"):
#                     continue
#                 nc_path = os.path.join(station_path, fname)
#                 try:
#                     station_code = derive_station_code(nc_path)
#                     date_str = extract_date_from_filename(nc_path)
#                     out_csv = out_csv_path(nc_path, station_code, date_str)
#                     if os.path.exists(out_csv):
#                         print(f"[SKIP] Exists: {out_csv}")
#                         continue
#                     print(f"[DO] {nc_path}")
#                     df = convert_nc_to_df(nc_path)
#                     ok, msg = basic_validate(df)
#                     if not ok:
#                         print(f"[WARN] Validation failed for {nc_path}: {msg}")
#                     ensure_dir(os.path.dirname(out_csv))
#                     df.to_csv(out_csv, index=False)
#                     print(f"[DONE] Wrote: {out_csv}")
#                 except Exception as e:
#                     print(f"[ERROR] {nc_path}: {e}")

# def main():
#     ensure_dir(PROCESSED_BASE_DIR)
#     print("[ALL] Starting full conversion across states/stations...")
#     process_all()
#     print("[ALL] Completed.")

# if __name__ == "__main__":
#     main()


[ALL] Starting full conversion across states/stations...
[DO] MERRA-2/MERRA-2_data_raw\Delhi\DL009_2021_2022\MERRA2_400.tavg1_2d_aer_Nx.20210101.SUB.nc
[DONE] Wrote: MERRA-2/MERRA-2_data_processed\Delhi\DL009_2021_2022\DL009_20210101_C1_full.csv
[DO] MERRA-2/MERRA-2_data_raw\Delhi\DL009_2021_2022\MERRA2_400.tavg1_2d_aer_Nx.20210102.SUB.nc
[DONE] Wrote: MERRA-2/MERRA-2_data_processed\Delhi\DL009_2021_2022\DL009_20210102_C1_full.csv
[DO] MERRA-2/MERRA-2_data_raw\Delhi\DL009_2021_2022\MERRA2_400.tavg1_2d_aer_Nx.20210103.SUB.nc
[DONE] Wrote: MERRA-2/MERRA-2_data_processed\Delhi\DL009_2021_2022\DL009_20210103_C1_full.csv
[DO] MERRA-2/MERRA-2_data_raw\Delhi\DL009_2021_2022\MERRA2_400.tavg1_2d_aer_Nx.20210104.SUB.nc
[DONE] Wrote: MERRA-2/MERRA-2_data_processed\Delhi\DL009_2021_2022\DL009_20210104_C1_full.csv
[DO] MERRA-2/MERRA-2_data_raw\Delhi\DL009_2021_2022\MERRA2_400.tavg1_2d_aer_Nx.20210105.SUB.nc
[DONE] Wrote: MERRA-2/MERRA-2_data_processed\Delhi\DL009_2021_2022\DL009_20210105_C1_full.cs

In [1]:
import os
import re
import sys
import pandas as pd
import xarray as xr

# ========== CONFIG ==========
RAW_BASE_DIR = "MERRA-2/MERRA-2_data_raw"
PROCESSED_BASE_DIR = "MERRA-2/MERRA-2_data_processed"
# Limit to these station folders (optional); set to [] to fill all missing
TARGET_STATION_FOLDERS = ["HR003_2021_2022", "KA002_2021_2022"]
VARS = ["BCEXTTAU", "DUEXTTAU", "OCEXTTAU", "SSEXTTAU", "SUEXTTAU", "TOTEXTTAU"]
REQUIRED_TIME_ROWS = 24
SKIP_DIR_SUFFIX = "_txt"
SKIP_DIR_EXACT = "state_txt"
ENGINES = ["netcdf4", "h5netcdf", "scipy"]  # try in this order
# ===========================

def ensure_dir(path: str):
    os.makedirs(path, exist_ok=True)

def should_skip_dir(name: str) -> bool:
    lname = name.lower()
    return lname == SKIP_DIR_EXACT or lname.endswith(SKIP_DIR_SUFFIX)

def derive_station_code(nc_path: str) -> str:
    # Parent folder like "HR003_2021_2022" -> "HR003"
    station_folder = os.path.basename(os.path.dirname(os.fspath(nc_path)))
    return station_folder[:5]

def extract_date_from_filename(nc_path: str) -> str:
    fname = os.path.basename(os.fspath(nc_path))
    m = re.search(r"\d{8}", fname)
    if not m:
        raise ValueError(f"Could not find 8-digit date in filename: {fname}")
    return m.group(0)

def out_csv_path(nc_path: str, station_code: str, date_str: str) -> str:
    station_path = os.path.dirname(os.fspath(nc_path))
    state_path = os.path.dirname(station_path)
    state = os.path.basename(state_path)
    station_folder = os.path.basename(station_path)
    out_name = f"{station_code}_{date_str}_C1_full.csv"
    return os.path.join(PROCESSED_BASE_DIR, state, station_folder, out_name)

def open_with_fallback(nc_path: str):
    last_err = None
    for eng in ENGINES:
        try:
            return xr.open_dataset(nc_path, decode_times=True, engine=eng)
        except Exception as e:
            last_err = e
    raise last_err  # re-raise last engine's error

def convert_nc_to_df_fallback(nc_path: str) -> pd.DataFrame:
    with open_with_fallback(nc_path) as ds:
        present = [v for v in VARS if v in ds.data_vars]
        if not present:
            raise ValueError(f"No requested variables present in {os.path.basename(nc_path)}; looked for {VARS}")
        df = ds[present].to_dataframe().reset_index()
    df["time"] = pd.to_datetime(df["time"], utc=True)
    df["hour_utc"] = df["time"].dt.hour
    df["time_utc"] = df["time"].dt.strftime("%Y-%m-%d %H:%M")
    station_code = derive_station_code(nc_path)
    n = len(df)
    out = pd.DataFrame({
        "station_code": [station_code] * n,
        "time_utc": df["time_utc"],
        "hour_utc": df["hour_utc"],
    })
    for v in VARS:
        out[v] = df[v] if v in df.columns else pd.NA
    return out

def basic_validate(df: pd.DataFrame):
    if "station_code" not in df.columns or "time_utc" not in df.columns or "hour_utc" not in df.columns:
        return False, "Missing required columns"
    if len(df) != REQUIRED_TIME_ROWS:
        return False, f"Unexpected rows: {len(df)} != {REQUIRED_TIME_ROWS}"
    for v in VARS:
        if v not in df.columns:
            return False, f"Missing variable column: {v}"
    return True, "OK"

def list_all_nc(root: str):
    nc_files = []
    for dirpath, dirnames, filenames in os.walk(root, topdown=True):
        dirnames[:] = [d for d in dirnames if not should_skip_dir(d)]
        for fname in filenames:
            if fname.endswith(".nc"):
                nc_files.append(os.path.join(dirpath, fname))
    return sorted(nc_files)

def find_missing(limit_to=None):
    all_nc = list_all_nc(RAW_BASE_DIR)
    if limit_to:
        all_nc = [p for p in all_nc if os.path.basename(os.path.dirname(p)) in limit_to]
    missing = []
    for nc_path in all_nc:
        try:
            station_code = derive_station_code(nc_path)
            date_str = extract_date_from_filename(nc_path)
            out_csv = out_csv_path(nc_path, station_code, date_str)
            if not os.path.exists(out_csv):
                missing.append((nc_path, out_csv))
        except Exception as e:
            print(f"[WARN] Skip (naming) {nc_path}: {e}")
    return missing

def fill_missing(missing_pairs):
    failed = []
    for nc_path, out_csv in missing_pairs:
        try:
            print(f"[FILL] {nc_path} -> {out_csv}")
            df = convert_nc_to_df_fallback(nc_path)
            ok, msg = basic_validate(df)
            if not ok:
                print(f"[WARN] Validation: {msg} -> {nc_path}")
            ensure_dir(os.path.dirname(out_csv))
            df.to_csv(out_csv, index=False)
            print(f"[DONE] {out_csv}")
        except Exception as e:
            print(f"[ERROR] {nc_path}: {e}")
            failed.append((nc_path, str(e)))
    if failed:
        print("\n[SUMMARY] Files needing re-download or manual check:")
        for path, err in failed:
            print(f"  - {path}\n    Reason: {err}")
    return failed

def main():
    print("[CHECK] Scanning missing (targeted)...")
    missing = find_missing(limit_to=TARGET_STATION_FOLDERS)
    if not missing:
        print("[CHECK] None missing in targeted folders.")
        return
    print("[CHECK] Missing outputs:")
    for nc_path, out_csv in missing:
        print(f"  - NC:  {nc_path}\n    OUT: {out_csv}")
    print(f"[FILL] Processing {len(missing)} missing file(s) with engine fallback...")
    failed = fill_missing(missing)
    print("[FILL] Completed.")
    if failed:
        print("[ACTION] Re-download the above files; HDF errors often indicate corruption.")
        # Optionally write a report file:
        # with open("refill_failed.txt","w") as f:
        #     for p,e in failed: f.write(f"{p}\t{e}\n")

if __name__ == "__main__":
    main()


[CHECK] Scanning missing (targeted)...
[CHECK] Missing outputs:
  - NC:  MERRA-2/MERRA-2_data_raw\Haryana\HR003_2021_2022\MERRA2_400.tavg1_2d_aer_Nx.20210207.SUB.nc
    OUT: MERRA-2/MERRA-2_data_processed\Haryana\HR003_2021_2022\HR003_20210207_C1_full.csv
  - NC:  MERRA-2/MERRA-2_data_raw\Karnataka\KA002_2021_2022\MERRA2_401.tavg1_2d_aer_Nx.20210818.SUB.nc
    OUT: MERRA-2/MERRA-2_data_processed\Karnataka\KA002_2021_2022\KA002_20210818_C1_full.csv
[FILL] Processing 2 missing file(s) with engine fallback...
[FILL] MERRA-2/MERRA-2_data_raw\Haryana\HR003_2021_2022\MERRA2_400.tavg1_2d_aer_Nx.20210207.SUB.nc -> MERRA-2/MERRA-2_data_processed\Haryana\HR003_2021_2022\HR003_20210207_C1_full.csv
[ERROR] MERRA-2/MERRA-2_data_raw\Haryana\HR003_2021_2022\MERRA2_400.tavg1_2d_aer_Nx.20210207.SUB.nc: cannot mmap an empty file
[FILL] MERRA-2/MERRA-2_data_raw\Karnataka\KA002_2021_2022\MERRA2_401.tavg1_2d_aer_Nx.20210818.SUB.nc -> MERRA-2/MERRA-2_data_processed\Karnataka\KA002_2021_2022\KA002_20210818_C

In [ ]:
# # Improved .nc to csv actual (bulk summaries)
# import os
# import re
# import sys
# import pandas as pd
# import xarray as xr

# # ========== CONFIG ==========
# RAW_BASE_DIR = "MERRA-2/MERRA-2_data_raw"             # root with state/station folders
# PROCESSED_BASE_DIR = "MERRA-2/MERRA-2_data_processed"  # output mirror
# VARS = ["BCEXTTAU", "DUEXTTAU", "OCEXTTAU", "SSEXTTAU", "SUEXTTAU", "TOTEXTTAU"]
# REQUIRED_TIME_ROWS = 24
# SKIP_DIR_SUFFIX = "_txt"
# SKIP_DIR_EXACT = "state_txt"
# VERBOSE = False  # set True to print each conversion; False prints only summaries
# # ===========================

# def ensure_dir(path: str):
#     os.makedirs(path, exist_ok=True)

# def should_skip_dir(name: str) -> bool:
#     lname = name.lower()
#     return lname == SKIP_DIR_EXACT or lname.endswith(SKIP_DIR_SUFFIX)

# def derive_station_code(nc_path: str) -> str:
#     # Parent folder like "DL009_2021_2022" -> "DL009"
#     station_folder = os.path.basename(os.path.dirname(os.fspath(nc_path)))
#     return station_folder[:5]

# def extract_date_from_filename(nc_path: str) -> str:
#     # Extract YYYYMMDD from NetCDF filename
#     fname = os.path.basename(os.fspath(nc_path))
#     m = re.search(r"\d{8}", fname)
#     if not m:
#         raise ValueError(f"Could not find 8-digit date in filename: {fname}")
#     return m.group(0)

# def out_csv_path(nc_path: str, station_code: str, date_str: str) -> str:
#     # processed/<state>/<station_folder>/<Stationcode_YYYYMMDD_C1_full.csv>
#     station_path = os.path.dirname(os.fspath(nc_path))
#     state_path = os.path.dirname(station_path)
#     state = os.path.basename(state_path)
#     station_folder = os.path.basename(station_path)
#     out_name = f"{station_code}_{date_str}_C1_full.csv"
#     return os.path.join(PROCESSED_BASE_DIR, state, station_folder, out_name)

# def convert_nc_to_df(nc_path: str) -> pd.DataFrame:
#     ds = xr.open_dataset(nc_path, decode_times=True)
#     present = [v for v in VARS if v in ds.data_vars]
#     if not present:
#         raise ValueError(f"No requested variables present in {os.path.basename(nc_path)}; looked for {VARS}")
#     df = ds[present].to_dataframe().reset_index()
#     df["time"] = pd.to_datetime(df["time"], utc=True)
#     df["hour_utc"] = df["time"].dt.hour
#     df["time_utc"] = df["time"].dt.strftime("%Y-%m-%d %H:%M")
#     station_code = derive_station_code(nc_path)
#     n = len(df)
#     out = pd.DataFrame({
#         "station_code": [station_code] * n,
#         "time_utc": df["time_utc"],
#         "hour_utc": df["hour_utc"],
#     })
#     for v in VARS:
#         out[v] = df[v] if v in df.columns else pd.NA
#     return out

# def basic_validate(df: pd.DataFrame):
#     if "station_code" not in df.columns or "time_utc" not in df.columns or "hour_utc" not in df.columns:
#         return False, "Missing required columns"
#     if len(df) != REQUIRED_TIME_ROWS:
#         return False, f"Unexpected rows: {len(df)} != {REQUIRED_TIME_ROWS}"
#     for v in VARS:
#         if v not in df.columns:
#             return False, f"Missing variable column: {v}"
#     return True, "OK"

# def process_station_folder(state_path: str, station_folder: str, totals):
#     station_path = os.path.join(state_path, station_folder)
#     if not os.path.isdir(station_path) or should_skip_dir(station_folder):
#         return
#     # Discover all .nc files in this station folder
#     all_nc = sorted([os.path.join(station_path, f) for f in os.listdir(station_path) if f.endswith(".nc")])
#     total_nc = len(all_nc)
#     processed_now = 0
#     already_exists = 0
#     failed = 0

#     for nc_path in all_nc:
#         try:
#             station_code = derive_station_code(nc_path)
#             date_str = extract_date_from_filename(nc_path)
#             out_csv = out_csv_path(nc_path, station_code, date_str)
#             if os.path.exists(out_csv):
#                 already_exists += 1
#                 if VERBOSE:
#                     print(f"[SKIP] Exists: {out_csv}")
#                 continue
#             df = convert_nc_to_df(nc_path)
#             ok, msg = basic_validate(df)
#             if not ok and VERBOSE:
#                 print(f"[WARN] Validation: {msg} -> {nc_path}")
#             ensure_dir(os.path.dirname(out_csv))
#             df.to_csv(out_csv, index=False)
#             processed_now += 1
#             if VERBOSE:
#                 print(f"[DONE] Wrote: {out_csv}")
#         except Exception as e:
#             failed += 1
#             print(f"[ERROR] {nc_path}: {e}")

#     done = processed_now + already_exists
#     not_processed = total_nc - done
#     print(f"{station_folder}: {done}/{total_nc} processed; Not processed: {not_processed}")  # summary line

#     # Update grand totals
#     totals["total_nc"] += total_nc
#     totals["done"] += done
#     totals["not_processed"] += not_processed
#     totals["failed"] += failed

# def process_all():
#     totals = {"total_nc": 0, "done": 0, "not_processed": 0, "failed": 0}
#     for state in sorted(os.listdir(RAW_BASE_DIR)):
#         state_path = os.path.join(RAW_BASE_DIR, state)
#         if not os.path.isdir(state_path) or should_skip_dir(state):
#             continue
#         for station in sorted(os.listdir(state_path)):
#             process_station_folder(state_path, station, totals)
#     print(f"TOTAL: {totals['done']}/{totals['total_nc']} processed; Not processed: {totals['not_processed']}; Failed: {totals['failed']}")

# def main():
#     ensure_dir(PROCESSED_BASE_DIR)
#     process_all()

# if __name__ == "__main__":
#     main()
